In [3]:
def Sweep_polytope(P):
    V = P.vertices()
    return sum([Polyhedron(vertices=[e[0], e[1]]) for e in Subsets(V, 2)])

In [11]:
def gamma(d, t):
    return vector([t^i for i in range(1, d+1)])

def Cyclic_polytope(d, tt):
    return Polyhedron(vertices = [gamma(d, t) for t in tt])

In [175]:
def sweep_from_lin_func(V, w, as_list_of_vector=False):
    if as_list_of_vector:
        W = list(V)
        W.sort(key = lambda x : sum(x[i]*w[i] for i in range(len(w))))
        return W
    W = list(V)
    W.sort(key = lambda x : sum(x[i]*w[i] for i in range(len(w))))
    return [W.index(x) for x in V]

def all_sweeps(P, as_list_of_vector=False):
    V = list(P.vertices())
    # print(V)
    CC = Sweep_polytope(P).normal_fan().generating_cones()
    for C in CC:
        w = sum(C.rays())
        yield sweep_from_lin_func(V, w, as_list_of_vector)

In [163]:
def AsDs_hyperplane_arrangement(n):
    H = HyperplaneArrangements(QQ, tuple('t'+str(i) for i in range(n)))
    H.inject_variables()
    AsDs_Arr = H()
    for S in Subsets(Subsets(range(n), 2), 2):
        if S[0][0] + S[0][1]/n < S[1][0] + S[1][1]/n:
            i, j = S[0]
            k, l = S[1]
        else:
            i, j = S[1]
            k, l = S[0]
        # print(i,j,k,l)
        AsDs_Arr = AsDs_Arr.add_hyperplane(eval("t"+str(i)) + eval("t"+str(j)) - eval("t"+str(k)) - eval("t"+str(l)))
    return AsDs_Arr

for n in range(3, 8):
    print("n =", n)
    AsDs_Arr = AsDs_hyperplane_arrangement(n)
    print(AsDs_Arr)
    print(AsDs_Arr.n_regions()/factorial(n))
    print()

n = 3
Defining t0, t1, t2
Arrangement <t1 - t2 | t0 - t1 | t0 - t2>
1

n = 4
Defining t0, t1, t2, t3
Arrangement of 9 hyperplanes of dimension 4 and rank 3
2

n = 5
Defining t0, t1, t2, t3, t4
Arrangement of 25 hyperplanes of dimension 5 and rank 4
12

n = 6
Defining t0, t1, t2, t3, t4, t5
Arrangement of 60 hyperplanes of dimension 6 and rank 5
168

n = 7
Defining t0, t1, t2, t3, t4, t5, t6


KeyboardInterrupt: 

In [111]:
def all_sweeps_prediction(d, tt):
    n = len(tt)
    for s in Permutations(n):
        if len([r for r in s.runs() if len(r) >= 2]) + len([r for r in s.decreasing_runs() if len(r) >= 2]) <= 2:
            s_ = s.inverse()
            As = s_.descents(positive=True)
            Ds = s_.descents()
            if len(As) == 0 or len(Ds) == 0:
                yield [x-1 for x in s]
            else:
                s_, As, Ds = [x-1 for x in s_], [x-1 for x in As], [x-1 for x in Ds]
                mp, Mp = min(tt[s_[i]] + tt[s_[i+1]] for i in As), max(tt[s_[i]] + tt[s_[i+1]] for i in As)
                mm, Mm = min(tt[s_[i]] + tt[s_[i+1]] for i in Ds), max(tt[s_[i]] + tt[s_[i+1]] for i in Ds)
                # R = Polyhedron(vertices = [(tt[s_[i]] + tt[s_[i+1]],) for i in As])
                # Q = Polyhedron(vertices = [(tt[s_[i]] + tt[s_[i+1]],) for i in Ds])
                # print(s, R, Q)
                if (Mp < mm) or (Mm < mp):
                    yield [x-1 for x in s]

In [194]:
def compl_sym_hom(ti, tj, dd):
    return sum(ti^a * tj^(dd-a) for a in range(dd+1))

def notin_forbiden_hypersurface(d, tt):
    n = len(tt)
    for dd in range(1, d):
        for S in Subsets(Subsets(range(n), 2), 2):
            i, j = S[0]
            k, l = S[1]
            if compl_sym_hom(tt[i], tt[j], dd) == compl_sym_hom(tt[k], tt[l], dd):
                return False
    return True

In [7]:
P = polytopes.cube()
print(P)
Sw = Sweep_polytope(P)
print(Sw)

A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 8 vertices
A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 96 vertices


In [24]:
P = polytopes.hypercube(4)
print(P)
Sw = Sweep_polytope(P)
print(Sw)

A 4-dimensional polyhedron in ZZ^4 defined as the convex hull of 16 vertices


KeyboardInterrupt: 

In [10]:
for n in range(1, 5):
    P = polytopes.simplex(n)
    print(P)
    Sw = Sweep_polytope(P)
    print(Sw)
    print(Sw.is_combinatorially_isomorphic(polytopes.permutahedron(n+1)))
    print()

A 1-dimensional polyhedron in ZZ^2 defined as the convex hull of 2 vertices
A 1-dimensional polyhedron in ZZ^2 defined as the convex hull of 2 vertices
True

A 2-dimensional polyhedron in ZZ^3 defined as the convex hull of 3 vertices
A 2-dimensional polyhedron in ZZ^3 defined as the convex hull of 6 vertices
True

A 3-dimensional polyhedron in ZZ^4 defined as the convex hull of 4 vertices
A 3-dimensional polyhedron in ZZ^4 defined as the convex hull of 24 vertices
True

A 4-dimensional polyhedron in ZZ^5 defined as the convex hull of 5 vertices
A 4-dimensional polyhedron in ZZ^5 defined as the convex hull of 120 vertices
True



In [12]:
from random import randint

In [185]:
d = 2

box = 150

C = []

for n in range(2, 16):
    print("n =", n)
    tt = []
    b = False
    while len(set(tt)) != n or not b:
        tt = [randint(0, box) for _ in range(n)]
        b = all([tt[S[0][0]] + tt[S[0][1]] != tt[S[1][0]] + tt[S[1][1]] for S in Subsets(Subsets(range(n), 2), 2)])
    tt.sort()
    print(tt)
    P = Cyclic_polytope(d, tt)
    print(P)
    Sw = Sweep_polytope(P)
    print(Sw)
    C.append(Sw.n_vertices())
    print("(n+1)*(n-2) =", (n+1)*(n-2))
    print()
    print(C)
    print()

n = 2
[0, 9]
A 1-dimensional polyhedron in ZZ^2 defined as the convex hull of 2 vertices
A 1-dimensional polyhedron in ZZ^2 defined as the convex hull of 2 vertices
(n+1)*(n-2) = 0

[2]

n = 3
[56, 58, 106]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 3 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 6 vertices
(n+1)*(n-2) = 4

[2, 6]

n = 4
[87, 103, 112, 119]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 4 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 12 vertices
(n+1)*(n-2) = 10

[2, 6, 12]

n = 5
[8, 41, 43, 69, 78]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 5 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 20 vertices
(n+1)*(n-2) = 18

[2, 6, 12, 20]

n = 6
[49, 78, 83, 85, 108, 147]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 6 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 30 vertices
(n+1)*(n

KeyboardInterrupt: 

In [23]:
d = 2

C = []

for n in range(2, 16):
    print("n =", n)
    tt = [2^i for i in range(1, n+1)]
    print(tt)
    P = Cyclic_polytope(d, tt)
    print(P)
    Sw = Sweep_polytope(P)
    print(Sw)
    C.append(Sw.n_vertices())
    print("(n+1)*(n-2) =", (n+1)*(n-2))
    print()
    print(C)
    print()

n = 2
[2, 4]
A 1-dimensional polyhedron in ZZ^2 defined as the convex hull of 2 vertices
A 1-dimensional polyhedron in ZZ^2 defined as the convex hull of 2 vertices
(n+1)*(n-2) = 0

[2]

n = 3
[2, 4, 8]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 3 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 6 vertices
(n+1)*(n-2) = 4

[2, 6]

n = 4
[2, 4, 8, 16]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 4 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 12 vertices
(n+1)*(n-2) = 10

[2, 6, 12]

n = 5
[2, 4, 8, 16, 32]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 5 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 20 vertices
(n+1)*(n-2) = 18

[2, 6, 12, 20]

n = 6
[2, 4, 8, 16, 32, 64]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 6 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 30 vertices
(n+1)*(n-2) = 28

[2, 6, 

In [ ]:
# [2, 6, 12, 20, 30, 42, 54, 70, 84, 98, 116, 136, 146]

In [21]:
[n*(n+1) for n in range(16)]

[0, 2, 6, 12, 20, 30, 42, 56, 72, 90, 110, 132, 156, 182, 210, 240]

In [186]:
d = 2
n = 10

box = 250

C = {}

for c in range(100):
    if (c+1) % 10 == 0:
        print(c+1)
    tt = []
    b = False
    while len(set(tt)) != n or not b:
        tt = [randint(0, box) for _ in range(n)]
        b = all([tt[S[0][0]] + tt[S[0][1]] != tt[S[1][0]] + tt[S[1][1]] for S in Subsets(Subsets(range(n), 2), 2)])
    tt.sort()
    #print(tt)
    P = Cyclic_polytope(d, tt)
    #print(P)
    Sw = Sweep_polytope(P)
    #print(Sw)
    N = Sw.n_vertices()
    if N in C:
        C[N] += 1
    else:
        C[N] = 1

print(C)

10
20
30
40
50
60
70
80
90
100
{90: 100}


In [188]:
d = 2
n = 12

box = 500

C = {}

for c in range(100):
    if (c+1) % 10 == 0:
        print(c+1)
        print(C)
    tt = []
    b = False
    while len(set(tt)) != n or not b:
        tt = [randint(0, box) for _ in range(n)]
        b = all([tt[S[0][0]] + tt[S[0][1]] != tt[S[1][0]] + tt[S[1][1]] for S in Subsets(Subsets(range(n), 2), 2)])
    tt.sort()
    #print(tt)
    P = Cyclic_polytope(d, tt)
    #print(P)
    Sw = Sweep_polytope(P)
    #print(Sw)
    N = Sw.n_vertices()
    if N in C:
        C[N] += 1
    else:
        C[N] = 1

print(C)

10
{132: 9}
20
{132: 19}
30
{132: 29}
40
{132: 39}
50
{132: 49}
60
{132: 59}
70
{132: 69}
80
{132: 79}
90
{132: 89}
100
{132: 99}
{132: 100}


In [61]:
P = polytopes.cube()
print(P)
for s in all_sweeps(P):
    print(s)

A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 8 vertices
[A vertex at (1, -1, -1), A vertex at (1, 1, -1), A vertex at (1, 1, 1), A vertex at (1, -1, 1), A vertex at (-1, -1, 1), A vertex at (-1, -1, -1), A vertex at (-1, 1, -1), A vertex at (-1, 1, 1)]
[4, 6, 7, 5, 1, 0, 2, 3]
[3, 1, 0, 2, 6, 7, 5, 4]
[2, 0, 1, 3, 7, 6, 4, 5]
[5, 7, 6, 4, 0, 1, 3, 2]
[4, 5, 7, 6, 2, 0, 1, 3]
[3, 2, 0, 1, 5, 7, 6, 4]
[1, 0, 2, 3, 7, 5, 4, 6]
[6, 7, 5, 4, 0, 2, 3, 1]
[5, 4, 6, 7, 3, 1, 0, 2]
[2, 3, 1, 0, 4, 6, 7, 5]
[0, 1, 3, 2, 6, 4, 5, 7]
[7, 6, 4, 5, 1, 3, 2, 0]
[6, 4, 5, 7, 3, 2, 0, 1]
[1, 3, 2, 0, 4, 5, 7, 6]
[0, 2, 3, 1, 5, 4, 6, 7]
[7, 5, 4, 6, 2, 3, 1, 0]
[3, 6, 7, 5, 1, 0, 2, 4]
[4, 1, 0, 2, 6, 7, 5, 3]
[2, 0, 1, 4, 7, 6, 3, 5]
[5, 7, 6, 3, 0, 1, 4, 2]
[3, 5, 7, 6, 2, 0, 1, 4]
[4, 2, 0, 1, 5, 7, 6, 3]
[1, 0, 2, 4, 7, 5, 3, 6]
[6, 7, 5, 3, 0, 2, 4, 1]
[5, 3, 6, 7, 4, 1, 0, 2]
[2, 4, 1, 0, 3, 6, 7, 5]
[0, 1, 4, 2, 6, 3, 5, 7]
[7, 6, 3, 5, 1, 4, 2, 0]
[6, 3, 5, 7, 4, 2, 0, 1]
[1

In [62]:
P = polytopes.simplex(3).affine_hull_projection()
print(P)
print(Sweep_polytope(P))
for s in all_sweeps(P):
    print(s)

A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 4 vertices
A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 24 vertices
[A vertex at (0, 0, 0), A vertex at (0, 0, 1), A vertex at (0, 1, 0), A vertex at (1, 0, 0)]
[0, 1, 2, 3]
[1, 0, 2, 3]
[0, 2, 1, 3]
[2, 0, 1, 3]
[1, 2, 0, 3]
[2, 1, 0, 3]
[0, 1, 3, 2]
[1, 0, 3, 2]
[3, 2, 1, 0]
[2, 3, 1, 0]
[0, 3, 1, 2]
[3, 1, 2, 0]
[1, 3, 2, 0]
[3, 0, 1, 2]
[1, 3, 0, 2]
[3, 1, 0, 2]
[0, 2, 3, 1]
[2, 0, 3, 1]
[0, 3, 2, 1]
[2, 1, 3, 0]
[1, 2, 3, 0]
[3, 0, 2, 1]
[3, 2, 0, 1]
[2, 3, 0, 1]


In [63]:
d = 2

for n in range(3, 16):
    print("n =", n)
    tt = [2^i for i in range(1, n+1)]
    print(tt)
    P = Cyclic_polytope(d, tt)
    print(P)
    Sw = Sweep_polytope(P)
    print(Sw)
    for s in all_sweeps(P):
        print(s, [s.index(i) for i in range(len(s))])
    print()

n = 3
[2, 4, 8]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 3 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 6 vertices
[A vertex at (2, 4), A vertex at (4, 16), A vertex at (8, 64)]
[0, 1, 2] [0, 1, 2]
[1, 0, 2] [1, 0, 2]
[0, 2, 1] [0, 2, 1]
[2, 1, 0] [2, 1, 0]
[2, 0, 1] [1, 2, 0]
[1, 2, 0] [2, 0, 1]

n = 4
[2, 4, 8, 16]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 4 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 12 vertices
[A vertex at (2, 4), A vertex at (4, 16), A vertex at (8, 64), A vertex at (16, 256)]
[0, 1, 2, 3] [0, 1, 2, 3]
[1, 0, 2, 3] [1, 0, 2, 3]
[2, 0, 1, 3] [1, 2, 0, 3]
[0, 1, 3, 2] [0, 1, 3, 2]
[3, 2, 1, 0] [3, 2, 1, 0]
[2, 1, 0, 3] [2, 1, 0, 3]
[2, 3, 1, 0] [3, 2, 0, 1]
[1, 3, 2, 0] [3, 0, 2, 1]
[3, 2, 0, 1] [2, 3, 1, 0]
[0, 2, 3, 1] [0, 3, 1, 2]
[3, 1, 0, 2] [2, 1, 3, 0]
[1, 2, 3, 0] [3, 0, 1, 2]

n = 5
[2, 4, 8, 16, 32]
A 2-dimensional polyhedron in ZZ^2 defined as the co

In [113]:
d = 2

for n in range(3, 11):
    print("n =", n)
    tt = [2^i for i in range(1, n+1)]
    print(tt)
    P = Cyclic_polytope(d, tt)
    print(P)
    Sw = Sweep_polytope(P)
    print(Sw)
    S1 = [s for s in all_sweeps_prediction(d, tt)]
    print("done S1")
    S2 = [s for s in all_sweeps(P)]
    print("done S2")
    print(all(x in S2 for x in S1))
    print(len(S1), len(S2))
    print()

n = 3
[2, 4, 8]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 3 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 6 vertices
done S1
[A vertex at (2, 4), A vertex at (4, 16), A vertex at (8, 64)]
done S2
True
6 6

n = 4
[2, 4, 8, 16]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 4 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 12 vertices
done S1
[A vertex at (2, 4), A vertex at (4, 16), A vertex at (8, 64), A vertex at (16, 256)]
done S2
True
12 12

n = 5
[2, 4, 8, 16, 32]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 5 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 20 vertices
done S1
[A vertex at (2, 4), A vertex at (4, 16), A vertex at (8, 64), A vertex at (16, 256), A vertex at (32, 1024)]
done S2
True
20 20

n = 6
[2, 4, 8, 16, 32, 64]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 6 vertices
A 2-dimensional polyhedron in ZZ^2 de

KeyboardInterrupt: 

In [114]:
d = 2

box = 150

C = []

for n in range(3, 11):
    print("n =", n)
    tt = []
    b = False
    while len(set(tt)) != n or not b:
        tt = [randint(0, box) for _ in range(n)]
        b = all([tt[S[0]] + tt[S[1]] != tt[S[2]] + tt[S[3]] for S in Subsets(range(n), 4)])
    tt.sort()
    print(tt)
    P = Cyclic_polytope(d, tt)
    print(P)
    Sw = Sweep_polytope(P)
    print(Sw)
    S1 = [s for s in all_sweeps_prediction(d, tt)]
    S2 = [s for s in all_sweeps(P)]
    print(all(x in S2 for x in S1))
    print(len(S1), len(S2))
    print()

n = 3
[26, 77, 141]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 3 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 6 vertices
[A vertex at (26, 676), A vertex at (77, 5929), A vertex at (141, 19881)]
True
6 6

n = 4
[3, 44, 67, 104]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 4 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 12 vertices
[A vertex at (3, 9), A vertex at (44, 1936), A vertex at (67, 4489), A vertex at (104, 10816)]
True
12 12

n = 5
[0, 2, 34, 104, 118]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 5 vertices
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 20 vertices
[A vertex at (0, 0), A vertex at (2, 4), A vertex at (34, 1156), A vertex at (104, 10816), A vertex at (118, 13924)]
True
20 20

n = 6
[4, 15, 47, 66, 69, 108]
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 6 vertices
A 2-dimensional polyhedron in ZZ^2 defined as

In [184]:
d = 2

for n in range(3, 10):
    print("n =", n)
    AsDs_Arr = AsDs_hyperplane_arrangement(n)
    print(AsDs_Arr)
    nbr = AsDs_Arr.n_regions()
    print("nb regions =", nbr/factorial(n),"=", nbr,"/",factorial(n))
    print()
    c = 1
    for C in AsDs_Arr.regions():
        tt = sum([r.vector() for r in C.rays()])
        if all(tt[i] < tt[i+1] for i in range(n-1)):
            print("region n°", c)
            print("tt =", tt)
            P = Cyclic_polytope(d, tt)
            Sw = Sweep_polytope(P)
            print("Sw:", Sw)
            print("Sweeps:")
            for s in all_sweeps(P):
                print(" ", s)
            print()
            c += 1
    print("_________________________")
    print()

n = 3
Defining t0, t1, t2
Arrangement <t1 - t2 | t0 - t1 | t0 - t2>
nb regions = 1 = 6 / 6

region n° 1
tt = (-1, 0, 1)
Sw: A 2-dimensional polyhedron in QQ^2 defined as the convex hull of 6 vertices
Sweeps:
  [0, 1, 2]
  [1, 0, 2]
  [0, 2, 1]
  [2, 1, 0]
  [2, 0, 1]
  [1, 2, 0]

_________________________

n = 4
Defining t0, t1, t2, t3
Arrangement of 9 hyperplanes of dimension 4 and rank 3
nb regions = 2 = 48 / 24

region n° 1
tt = (-3, -1, 0, 1)
Sw: A 2-dimensional polyhedron in QQ^2 defined as the convex hull of 12 vertices
Sweeps:
  [0, 1, 2, 3]
  [0, 1, 3, 2]
  [1, 0, 2, 3]
  [3, 2, 1, 0]
  [3, 2, 0, 1]
  [2, 3, 1, 0]
  [0, 2, 3, 1]
  [0, 3, 2, 1]
  [2, 0, 1, 3]
  [3, 1, 0, 2]
  [3, 0, 1, 2]
  [1, 3, 2, 0]

region n° 2
tt = (-4, -3, -2, 0)
Sw: A 2-dimensional polyhedron in QQ^2 defined as the convex hull of 12 vertices
Sweeps:
  [0, 1, 2, 3]
  [1, 0, 2, 3]
  [0, 1, 3, 2]
  [2, 0, 1, 3]
  [3, 2, 1, 0]
  [2, 3, 1, 0]
  [2, 1, 0, 3]
  [3, 2, 0, 1]
  [0, 2, 3, 1]
  [1, 3, 2, 0]
  [1, 2

KeyboardInterrupt: 

In [145]:
var("x0")
var("x1")
var("x2")
var("x3")
H = HyperplaneArrangements(QQ, tuple('z'+str(i) for i in range(4)))
H.inject_variables()
#H = HyperplaneArrangements(QQ, ['x'+str(i) for i in range(3)])
Arr = H()
Arr = Arr.add_hyperplane(z1-z2)
Arr

Defining z0, z1, z2, z3


Arrangement <z1 - z2>

In [153]:
n = 4
for S in Subsets(Subsets(range(n), 2), 2):
    print(S, S[0][0] + S[0][1]/n < S[1][0] + S[1][1]/n)

{{0, 1}, {0, 2}} True
{{0, 1}, {0, 3}} True
{{0, 1}, {1, 2}} True
{{0, 1}, {1, 3}} True
{{0, 1}, {2, 3}} True
{{0, 2}, {0, 3}} True
{{0, 2}, {1, 2}} True
{{0, 2}, {1, 3}} True
{{0, 2}, {2, 3}} True
{{1, 2}, {0, 3}} False
{{1, 3}, {0, 3}} False
{{2, 3}, {0, 3}} False
{{1, 3}, {1, 2}} False
{{2, 3}, {1, 2}} False
{{1, 3}, {2, 3}} True


In [198]:
d = 3
n = 10

box = 500

C = {}

for c in range(100):
    if (c+1) % 10 == 0:
        print(c+1)
        print(C)
    tt = []
    b = False
    while len(set(tt)) != n or not notin_forbiden_hypersurface(d, tt):
        tt = [randint(0, box) for _ in range(n)]
    tt.sort()
    print(tt)
    #print(tt)
    P = Cyclic_polytope(d, tt)
    print(P)
    #print(P)
    Sw = Sweep_polytope(P)
    print(Sw)
    #print(Sw)
    N = Sw.n_vertices()
    if N in C:
        C[N] += 1
    else:
        C[N] = 1

print(C)

[5, 24, 204, 274, 294, 340, 403, 418, 443, 478]
A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 10 vertices
A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 1742 vertices
[84, 139, 143, 174, 220, 254, 354, 470, 487, 495]
A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 10 vertices
A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 1742 vertices
[10, 59, 69, 98, 105, 165, 202, 323, 437, 499]
A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 10 vertices
A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 1742 vertices
[17, 45, 72, 111, 163, 232, 253, 272, 365, 382]
A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 10 vertices
A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 1738 vertices
[78, 134, 172, 261, 267, 310, 320, 322, 385, 408]
A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 10 vertices
A 3-dimensional polyhedron in ZZ^3 defined as the convex

In [205]:
tt = [17, 45, 72, 111, 163, 232, 253, 272, 365, 382]
for S in Subsets(Subsets(range(n), 2), 3):
    if matrix([[compl_sym_hom(tt[S[i][0]], tt[S[i][1]], dd) for i in range(d)] for dd in range(d)]).det() == 0:
        print(S)

{{0, 1}, {0, 2}, {1, 2}}
{{0, 1}, {1, 3}, {0, 3}}
{{0, 1}, {1, 4}, {0, 4}}
{{0, 1}, {1, 5}, {0, 5}}
{{1, 6}, {0, 1}, {0, 6}}
{{0, 7}, {0, 1}, {1, 7}}
{{0, 1}, {8, 1}, {0, 8}}
{{0, 1}, {1, 9}, {0, 9}}
{{0, 2}, {2, 3}, {0, 3}}
{{2, 4}, {0, 2}, {0, 4}}
{{0, 2}, {2, 5}, {0, 5}}
{{0, 2}, {0, 6}, {2, 6}}
{{0, 7}, {0, 2}, {2, 7}}
{{8, 2}, {0, 2}, {0, 8}}
{{0, 2}, {9, 2}, {0, 9}}
{{3, 4}, {0, 4}, {0, 3}}
{{0, 5}, {3, 5}, {0, 3}}
{{3, 6}, {0, 6}, {0, 3}}
{{0, 7}, {3, 7}, {0, 3}}
{{8, 3}, {0, 8}, {0, 3}}
{{9, 3}, {0, 9}, {0, 3}}
{{4, 5}, {0, 4}, {0, 5}}
{{4, 6}, {0, 6}, {0, 4}}
{{0, 7}, {0, 4}, {4, 7}}
{{8, 4}, {0, 8}, {0, 4}}
{{9, 4}, {0, 4}, {0, 9}}
{{5, 6}, {0, 6}, {0, 5}}
{{0, 7}, {5, 7}, {0, 5}}
{{8, 5}, {0, 8}, {0, 5}}
{{9, 5}, {0, 9}, {0, 5}}
{{0, 7}, {6, 7}, {0, 6}}
{{8, 6}, {0, 6}, {0, 8}}
{{9, 6}, {0, 6}, {0, 9}}
{{0, 7}, {0, 8}, {8, 7}}
{{0, 7}, {9, 7}, {0, 9}}
{{8, 9}, {0, 8}, {0, 9}}
{{1, 3}, {2, 3}, {1, 2}}
{{2, 4}, {1, 4}, {1, 2}}
{{1, 5}, {2, 5}, {1, 2}}
{{1, 6}, {1, 2}, {2, 6}}


In [207]:
tt = [67, 97, 128, 153, 170, 298, 305, 346, 415, 448]
uu = [17, 45, 72, 111, 163, 232, 253, 272, 365, 382]
for S in Subsets(Subsets(range(n), 2), 3):
    if matrix([[compl_sym_hom(uu[S[i][0]], uu[S[i][1]], dd) for i in range(d)] for dd in range(d)]).det() == 0:
        if matrix([[compl_sym_hom(tt[S[i][0]], tt[S[i][1]], dd) for i in range(d)] for dd in range(d)]).det() != 0:
            print(S)

{{1, 4}, {1, 5}, {2, 6}}
{{4, 5}, {1, 4}, {2, 6}}
{{4, 5}, {1, 5}, {2, 6}}


In [211]:
S = [[1, 4], [1, 5], [2, 6]]
print(matrix([[compl_sym_hom(uu[S[i][0]], uu[S[i][1]], dd) for i in range(d)] for dd in range(d)]))
print(matrix([[compl_sym_hom(uu[S[i][0]], uu[S[i][1]], dd) for i in range(d)] for dd in range(d)]).det())
print()
print(matrix([[compl_sym_hom(tt[S[i][0]], tt[S[i][1]], dd) for i in range(d)] for dd in range(d)]))
print(matrix([[compl_sym_hom(tt[S[i][0]], tt[S[i][1]], dd) for i in range(d)] for dd in range(d)]).det())

[    1     1     1]
[  208   277   325]
[35929 66289 87409]
0

[     1      1      1]
[   267    395    433]
[ 54799 127119 148449]
-17920


In [222]:
d = 3
print(matrix([gamma(d, uu[S[i][0]]) - gamma(d, uu[S[i][1]]) for i in range(d)]).T)
print(matrix([gamma(d, uu[S[i][0]]) - gamma(d, uu[S[i][1]]) for i in range(d)]).det())
print()
print(matrix([gamma(d, tt[S[i][0]]) - gamma(d, tt[S[i][1]]) for i in range(d)]).T)
print(matrix([gamma(d, tt[S[i][0]]) - gamma(d, tt[S[i][1]]) for i in range(d)]).det())
print()

[     -118      -187      -181]
[   -24544    -51799    -58825]
[ -4239622 -12396043 -15821029]
0

[      -73      -201      -177]
[   -19491    -79395    -76641]
[ -4000327 -25550919 -26275473]
46540408320



In [224]:
print([[tt[j] for j in S[i]] for i in range(3)])

[[97, 170], [97, 298], [128, 305]]


In [226]:
46540408320/( (170-97) * (298-97) * (305-128) )

17920

In [200]:
M = matrix([[1, 2], [4, 3]])
M.det()

-5

In [227]:
print(5)
print(5)

5
5


In [230]:
for d in range(2, 8):
    print("d =", d)
    C = []
    for n in range(d+1, 10):
        print("n =", n)
        tt = [2^(i+1) for i in range(n)]
        P = Cyclic_polytope(d, tt)
        Sw = Sweep_polytope(P)
        print(Sw)
        C.append(Sw.n_vertices())
    print()
    print(C)
    print()

d = 2
n = 3
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 6 vertices
n = 4
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 12 vertices
n = 5
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 20 vertices
n = 6
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 30 vertices
n = 7
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 42 vertices
n = 8
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 56 vertices
n = 9
A 2-dimensional polyhedron in ZZ^2 defined as the convex hull of 72 vertices

[6, 12, 20, 30, 42, 56, 72]

d = 3
n = 4
A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 24 vertices
n = 5
A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 72 vertices
n = 6
A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 172 vertices
n = 7
A 3-dimensional polyhedron in ZZ^3 defined as the convex hull of 352 vertices
n = 8
A 3-dimensional polyhedron in ZZ^3 def

KeyboardInterrupt: 